# Multiple filter technique

An alternative to the moving window method is the multiple filter technique. Instead of moving a window in the time domain, a window is moved in the frequency domain. Of course, a window in the frequency domain is a filter, and hence the name of the method. Let $H_k(\omega,\omega_k)$ be the transfer function of the $k$-th filter centered on frequency $\omega_k$. Applying the filter involves multiplication of the filter transfer function with the Fourier transform of the time signal and then performing an inverse Fourier transform:
\begin{align}
f_k(t) = \int_{-\infty}^\infty\,H_k(\omega,\omega_k)F(\omega)\exp(i\omega t)\frac{d\omega}{2\pi} \,.
\end{align}
Basically, one could plot the resulting time series against the associated center frequency of the filter. However, $f_k(t)$ can also assume negative values. It would be better to plot the envelope of $f_k(t)$.

### The analytic signal
This can be obtained by constructing the analytic signal $z_k(t)$ of $f_k(t)$. It is a complex
signal whose real part is the original signal and whose imaginary part is its Hilbert transform. Its absolute
value is the envelope or instantaneous amplitude and its phase is the instantaneous phase:
\begin{align}
z_k(t) = a_k(t)\exp(i\Phi_k(t)) = f_k(t)+iq_k(t) \ \mathrm{with}\ q_k(t) = HT\{f_k(t)\}\,,
\end{align}
and
\begin{align}
a_k(t) = \sqrt{f_k(t)^2+q_k(t)^2},\ \Phi_k(t) = \arctan\left(\frac{q_k(t)}{f_k(t)}\right) \,.
\end{align}

The Hilbert transform can again easily be obtained because its Fourier transform is:
\begin{align}
Q_k(\omega) = i\,\mathrm{sign}(\omega)F_k(\omega)\,.
\end{align}
where $F_k(\omega)$ is the Fourier transform of $f_k(t)$. Inverse Fourier transform of $Q_k(\omega)$ gives the Hilbert transform of $f_k(t)$.

### Work flow
So the work flow of the multiple filter technique is as follows:
1. Compute Fourier transform of $f(t)$: $F(\omega)$.
2. Multiply $F(\omega)$ with bandpass filters $H_k(\omega,\omega_k)$ to obtain $F_k(\omega)$.
3. Compute Fourier transform of the Hilbert transform: $Q_k(\omega)=iF_k(\omega)$.
4. Transform both back to the time domain.
5. Calculate the instantaneous amplitude $a_k(t)$ and phase $\Phi_k(t)$.
6. Plot $a_k(t)$ in the time-frequency plane.

### Gaussian filters
One frequently made choice for the bandpass filters is a Gaussian function of the form:
\begin{align}
H_k(\omega,\omega_k) = e^{-\alpha\left(\frac{\omega-\omega_k}{\omega_k}\right)^2}
\end{align}
with inverse Fourier transform (impulse response):
\begin{align}
h_k(t) = \frac{\sqrt{\pi}\omega_k}{2\alpha}e^{-\frac{\omega_k^2t^2}{4\alpha}}\cos\omega_k t \,.
\end{align}
This Fourier transform pair demonstrates a fundamental property of spectral analysis:
Choosing $\alpha$ large gives a very narrow-banded filter but a very
long impulse response. Choosing $\alpha$ small gives a wide-banded filter but a very short 
impulse response. This is an expression of the uncertainty principle. If the frequency of a signal
is known very well, the signal is distributed over time. On the other hand, an impulse in the time domain has
a constant spectrum, i.e. the frequency is entirely unknown. In quantum mechanics, there is the energy-time
uncertainty relation, where energy $E=\hbar\omega$.

### Time and frequency resolution
The Gaussian Fourier transform pair has a special property. If we measure the duration of the impulse response by
\begin{align}
D_t^2 = \int_{-\infty}^\infty t^2 |h(t)|^2 dt
\end{align}
and the spread of the filter transfer function by
\begin{align}
D_\omega^2 = \int_{-\infty}^\infty \omega^2 |H(\omega)|^2 \frac{d\omega}{2\pi}\,,
\end{align}
then the product
\begin{align}
D_t D_\omega \ge \frac{1}{2} \,.
\end{align}
For the Gaussian filter, equality holds. Hence, the Gaussian filter is the one with the
best compromise between bandwidth and duration.

In [ ]:
# Preparation: load packages
import os
from obspy.core import read
from obspy.core import UTCDateTime
import numpy as np
import matplotlib.pylab as plt

In [ ]:
# Multiple filter analysis
def multipleFilterAnalysis(data,alfa,cfreq,dt,ndec):
    """
    Perform a multiple filter analysis of data.
    data:  Array of detrended and demeaned data whose length is power of 2 
    alfa:  Width parameter of Gaussian bandpass filter
    cfreq: Array of center frequencies of Gaussian filter
    dt: sampling interval of data
    ndec: decimation factor for instantaneous amplitude output
    """
    npts = len(data)
    nd = int(pow(2, np.ceil(np.log(npts)/np.log(2))))   # find next higher power of 2 of npts
    ftd = np.fft.rfft(data,nd)                   # Fourier transform of entire data set (pos. freq.)
                                                 # data are padded with zeros since npts <= nd
    freq = np.fft.rfftfreq(nd,dt)                # Fourier frequencies (positive frequencies)
    jf = 0                                       # center frequency counter
    mfa = np.zeros((len(cfreq),npts//ndec+1))    # numpy array for MFA result
    for cf in cfreq:
        hg = np.exp(-alfa*((freq-cf)/cf)**2)     # Gaussian filter (use f instead of omega here)
        fk = hg*ftd                              # multiply FT of data with filter
        qk = np.complex(0,1)*fk                  # FT of Hilbert transform
        ftk = np.fft.irfft(fk)                   # filtered data
        qtk = np.fft.irfft(qk)                   # Hilbert transform of filtered data
        at = np.sqrt(ftk**2+qtk**2)              # instantaneous amplitude
        mfa[jf,:] = at[0:npts:ndec]              # store decimated original result
        jf = jf+1                                # increase center frequency count
    return mfa

In [ ]:
# normalize multiple filter result either along time or frequency axis
def normalizeMFT(mfa,mode,exp):
    """
    Normalize the result of the mutiple filtering operation.
    mfa: array with instantaneous amplitudes versus frequency (mfa(f,t))
    mode: normalization mode: if 'time', normalize along time axis
          else normalize along frequency axis
    exp:  exponent for modifying inst amp using a power less than 1
    """
    nf,nt = mfa.shape
    if mode == 'time':
        for jf in range(0,nf):
            mfamax = np.amax(mfa[jf,:])
            mfa[jf,:] = np.power(mfa[jf,:]/mfamax+1.e-10,exp)          
    else:
        for jt in range(0,nt):
            mfamax = np.amax(mfa[:,jt])
            mfa[:,jt] = np.power(mfa[:,jt]/mfamax+1.e-10,exp)
    return mfa

In [ ]:
# borehole data from stations, Jan 23 2013
station = 'GEO2'                                    # station code
#  available stations are GEO2, GEO3 (only 14:00), GEO4, GEO5, GEO6, GEO7

record = '1400'                                     # record starting at 1400
stime = UTCDateTime('2013-01-23 14:17:00Z')         # use record starting at 1400
etime = UTCDateTime('2013-01-23 14:19:00Z')
ttitle = ', depth: 56.5 m'
    
datapath = "../data/{}/{}".format(station, 'e*'+record+'*.HHZ')      # search string for database
st = read(datapath)                                  # read file using obspy read
print(st)

st.trim(stime,etime)      # trim data stream to desired start and end time
st.detrend('linear')      # do a linear detrending
st.detrend('demean')      # subtract mean value
tr = st[0]                # extract first trace from stream (there is only one)
tr.plot();                # plot trace

In [ ]:
# prepare multiple filtering
alfa = 1000.0                                         # filter width parameter
npts = tr.stats.npts                                   # number of samples in time series
dt = tr.stats.delta                                    # sampling interval
fmax = 1./(2.*dt)                                      # Nyquist frequency
nd = int(pow(2, np.ceil(np.log(npts)/np.log(2))))      # find next higher power of 2 of npts
print("Number of samples: ",npts,                      # print some information about time series
      "\nSampling interval: ",dt,
      "\nNumber of samples with padding: ",nd,
      "\nMax. frequency: ",fmax)
cfreq = np.linspace(1.,fmax,1000)                       # array of filter center frequencies
freq = np.fft.rfftfreq(nd,dt)

In [ ]:
ndec = 100                                                # decimation factor for inst amplitude
mfa = multipleFilterAnalysis(tr.data,alfa,cfreq,dt,ndec)

In [ ]:
mfa = normalizeMFT(mfa,'freq',0.5)

In [ ]:
# plot the result
extent = (0.,npts*dt,fmax,1.)                         # extent of matrix in true time and frequency
plt.figure(figsize = [15,6])
plt.imshow(mfa,extent = extent,aspect=0.25)           # do plotting
plt.xlabel('Time [s]')
plt.ylabel('Center frequency [Hz]')
plt.show()

In [ ]:
# plot Gaussian filters
cf = 0.5*fmax
plt.figure(figsize = [15,4])
for alfa in [10,100,1000,10000,100000]:
    hg = np.exp(-alfa*((freq-cf)/cf)**2)     # Gaussian filter (use f instead of omega here)
    plt.plot(freq,hg)
plt.show()

# Exercise

1. Study the effect of $\alpha$ on the result of the multiple filtering
2. Think about the numerical effort of MFT in comparison with the moving window technique
3. Perform the analysis for different stations
4. Do you have some ideas why the results look different? What role plays normalization? Try to change the code such that each spectrum is normalized and not each instantaneous amplitude series.